# Import necessary functions

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import sklearn.metrics as metrics
import numpy as np
from sklearn.neighbors import NearestNeighbors
from scipy.spatial.distance import correlation, cosine
import ipywidgets as widgets
from IPython.display import display, clear_output
from sklearn.metrics import pairwise_distances
from sklearn.metrics import mean_squared_error
from math import sqrt
import sys, os
from contextlib import contextmanager
global k,metric

# Read files

In [68]:
#read the filtered original customer list - only contain customers that have spent over $5000
customer=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//target_customer.csv')

In [3]:
#read the file of products' purchase frequency
appearance=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//product_appearance.csv')

In [93]:
#read the file of incremental sales of products
increments=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//incremental_sales.csv')

In [59]:
#read the file of products' profitability and promotion-sensitivity
profit_sensit=pd.read_csv('https://s3.amazonaws.com/for-large-files/markting/customer_list.csv')

In [60]:
profit_sensit

Unnamed: 0  V1.x   cust_id  cust_profit_percent  V1.y  promo_sensitivity
0              1     1    799924             0.601062     1           0.582936
1              2     2   1889991             0.555647     2           0.588101
2              3     3   2109544             0.653533     3           0.637041
3              4     4   7629630             0.718448     4           0.511526
4              5     5   7669833             0.645166     5           0.539621
5              6     6   7739787             0.542865     6           0.622744
6              7     7   8639635             0.590567     7           0.730815
7              8     8  10329832             0.529129     8           0.683979
8              9     9  11789884             0.614343     9           0.708160
9             10    10  16739664             0.613607    10           0.669192
10            11    11  16829885             0.571340    11           0.655413
11            12    13  18539540             0.564836    13           0.553069
12            13    14  18909750             0.653475    14           0.662292
13            14    15  21159716             0.618175    15           0.645977
14            15    16  21579922             0.630306    16           0.727567
15            16    17  24179544             0.600163    17           0.726393
16            17    18  26499927             0.504000    18           0.632047
17            18    19  26769899             0.672414    19           0.657809
18            19    20  27999642             0.669195    20           0.573490
19            20    22  31879773             0.593624    22           0.607914
20            21    23  37359574             0.629373    23           0.727807
21            22    24  37449943             0.591428    24           0.758604
22            23    26  38479729             0.588193    26           0.572558
23            24    27  38959697             0.631720    27           0.525667
24            25    28  41459822             0.571503    28           0.642295
25            26    30  41709604             0.503041    30           0.616316
26            27    31  41709665             0.562968    31           0.569529
27            28    33  43769997             0.585856    33           0.548336
28            29    35  47779590             0.618842    35           0.664965
29            30    36  50759829             0.621505    36           0.528152
30            31    37  51079908             0.644099    37           0.578539
31            32    38  52039852             0.627965    38           0.641752
32            33    41  55699764             0.627651    41           0.516617
33            34    42  56659977             0.590396    42           0.524338
34            35    43  56969964             0.631826    43           0.584170
35            36    44  58159515             0.544515    44           0.553931
36            37    45  59719949             0.588272    45           0.786273
37            38    46  61279763             0.637378    46           0.565552
38            39    47  62949989             0.590094    47           0.615467
39            40    48  63039914             0.658258    48           0.562543
40            41    49  64599801             0.615810    49           0.597004
41            42    50  66789769             0.638061    50           0.572300
42            43    51  68009981             0.539108    51           0.610979
43            44    52  68299561             0.595723    52           0.548378
44            45    53  72549599             0.602222    53           0.535301
45            46    54  72729561             0.635944    54           0.534003
46            47    55  74049890             0.611688    55           0.606166
47            48    56  75339977             0.707290    56           0.530725
48            49    58  78669634             0.636991    58           0.623263
49            50    59  79309672             0.596743   

In [112]:
#combine 6 individual files that we ran from 6 notebooks to speed up the process
one=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//11.csv')
two=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//22.csv')
three=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//33.csv')
four=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//44.csv')
five=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//55.csv')
six=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//66.csv')
all_d=one.append(two).append(three).append(four).append(five).append(six)

In [114]:
all_d.to_csv('all_d.csv')

In [113]:
all_d

Unnamed: 0    product  ExpectedValue  customer
0            932  999885829      15.979170     29568
1           1154  999378733      10.383786     29568
2            222  999424824       7.901821     29568
3            490  999630595       7.307988     29568
4           1747  999749460       7.085252     29568
5           1607  999953616      15.939815     29909
6            949  999885829      12.783336     29909
7            327  999457945      10.540765     29909
8           1839  999364679       9.481684     29909
9           1768  999749460       8.097431     29909
10          1483  999953616      12.751852     39856
11           193  999424824      10.865004     39856
12          1113  999378733      10.383786     39856
13           889  999885829       7.989585     39856
14           272  999457945       7.905574     39856
15          1345  999953616      22.315741    289996
16           776  999885829      11.185419    289996
17          1485  999749460      11.133967    289996
18           826  999943438      10.024679    289996
19          1486  999749463       9.031940    289996
20          1549  999953616      19.127778    329968
21          1705  999749460      11.133967    329968
22           298  999457945      10.540765    329968
23           221  999424824       9.877277    329968
24           913  999885829       9.587502    329968
25          1068  999378733      14.710363    339627
26           862  999885829      12.783336    339627
27          1436  999953616      12.751852    339627
28           211  999424824      10.865004    339627
29           872  999148584       8.835463    339627
30           556  999958544      12.147394    550000
31           781  153701005      11.325972    550000
32          1128  999378733      11.249101    550000
33           910  999885829      11.185419    550000
34          1533  999953616       9.563889    550000
35          1526  999953616      19.127778    559804
36          1129  999378733      10.383786    559804
37           901  999885829       9.587502    559804
38           480  999630595       7.307988    559804
39          1682  999749469       7.287753    559804
40          1551  999953616      19.127778    709543
41          1135  999378733      11.249101    709543
42           219  999424824      10.865004    709543
43           568  999958544       9.447973    709543
44          2031  999938977       8.855856    709543
45          1584  999953616      25.503704    749639
46          1167  999378733      13.845048    749639
47           609  999958544      10.797684    749639
48          1736  999749463       9.031940    749639
49           349  999662852       8.555186    749639
50          1745  999953616      28.691667    769883
51          1039  999885829      12.783336    769883
52          1281  999378733       9.518470    769883
53          1986  999364679       9.481684    769883
54           893  153701005       8.494479    769883
55          1480  999953616      28.691667    799924
56          1086  999378733      15.575679    799924
57           530  999958544      10.797684    799924
58           925  999943438       8.592582    799924
59          1639  999749469       8.016529    799924
60          1153  999953616      12.751852    989587
61          1271  999749463      11.612495    989587
62           822  999378733      10.383786    989587
63          1275  999749469       8.016529    989587
64           237  999662852       7.604610    989587
65          1194  999953616      12.751852   1139738
66           881  999378733      11.249101   1139738
67           758  999943438      10.024679   1139738
68          1389  999274617       9.630577   1139738
69           713  999885829       9.587502   1139738
70          1670  999953616      19.127778   1179795
71           621  999958544      18.895947   1179795
72          1232  999378733      10.383786   1179795
73           241  999424824       8.889549   1179795
74            71  999579934    

# Data Exploration and Cleaning

In [109]:
#filter customers based on profitability and promotion sensitivity by a threshold of 0.55
profit_sensit=profit_sensit[profit_sensit['promo_sensitivity']>0.5]
profit_sensit=profit_sensit[profit_sensit['cust_profit_percent']>0.5]

In [110]:
profit_sensit

Unnamed: 0  V1.x   cust_id  cust_profit_percent  V1.y  promo_sensitivity
0              1     1    799924             0.601062     1           0.582936
1              2     2   1889991             0.555647     2           0.588101
2              3     3   2109544             0.653533     3           0.637041
6              7     7   8639635             0.590567     7           0.730815
8              9     9  11789884             0.614343     9           0.708160
9             10    10  16739664             0.613607    10           0.669192
10            11    11  16829885             0.571340    11           0.655413
11            12    13  18539540             0.564836    13           0.553069
12            13    14  18909750             0.653475    14           0.662292
13            14    15  21159716             0.618175    15           0.645977
14            15    16  21579922             0.630306    16           0.727567
15            16    17  24179544             0.600163    17           0.726393
17            18    19  26769899             0.672414    19           0.657809
18            19    20  27999642             0.669195    20           0.573490
19            20    22  31879773             0.593624    22           0.607914
20            21    23  37359574             0.629373    23           0.727807
21            22    24  37449943             0.591428    24           0.758604
22            23    26  38479729             0.588193    26           0.572558
24            25    28  41459822             0.571503    28           0.642295
26            27    31  41709665             0.562968    31           0.569529
28            29    35  47779590             0.618842    35           0.664965
30            31    37  51079908             0.644099    37           0.578539
31            32    38  52039852             0.627965    38           0.641752
34            35    43  56969964             0.631826    43           0.584170
36            37    45  59719949             0.588272    45           0.786273
37            38    46  61279763             0.637378    46           0.565552
38            39    47  62949989             0.590094    47           0.615467
39            40    48  63039914             0.658258    48           0.562543
40            41    49  64599801             0.615810    49           0.597004
41            42    50  66789769             0.638061    50           0.572300
46            47    55  74049890             0.611688    55           0.606166
48            49    58  78669634             0.636991    58           0.623263
49            50    59  79309672             0.596743    59           0.586320
51            52    61  81519841             0.616175    61           0.562141
52            53    62  81879929             0.634281    62           0.709577
53            54    63  82639994             0.590448    63           0.610583
54            55    65  84299911             0.624045    65           0.647602
55            56    66  85149539             0.609190    66           0.608858
56            57    67  87629985             0.668398    67           0.744600
57            58    68  89729948             0.585781    68           0.698917
58            59    70  91139797             0.639885    70           0.647654
59            60    71  93379871             0.594871    71           0.568096
60            61    72  93789936             0.630414    72           0.853352
62            63    74  99439924             0.736866    74           0.773455
63            64    75   2029760             0.675659    75           0.732488
65            66    78   9089753             0.619082    78           0.703228
66            67    79  10519992             0.672349    79           0.660351
67            68    80  11879968             0.768143    80           0.613757
68            69    81  13559676             0.657513    81           0.578283
69            70    82  15310000             0.599620   

In [117]:
#only select the customers that have high profitability and high sensitivity
customer=customer[customer['cust_id'].isin(profit_sensit['cust_id'])]

IndexError: invalid index to scalar variable.

In [31]:
increments.head(5)

prod_id  incremental
0  145519008    -3.790432
1  145519009     9.949572
2  145519010    27.096736
3  145519011   -54.861296
4  145519012   -25.376284

In [32]:
appearance.head(5)

Unnamed: 0    prod_id    N
0           1  145519008  103
1           2  145519009  182
2           3  145519010   98
3           4  145519011  122
4           5  145519012  244

In [33]:
appearance['N'].describe()

count     6852.000000
mean       312.354787
std       1363.508309
min          1.000000
25%         39.000000
50%         96.000000
75%        246.000000
max      73374.000000
Name: N, dtype: float64

In [71]:
#filter out products that are bought less than 15 times
appearance_filtered=appearance[appearance['N']>15]
customer=customer[customer['prod_id'].isin(appearance_filtered['prod_id'])]

In [6]:
#make sure we can see the full columns and all rows
pd.set_option('display.max_colwidth', 1000)
pd.set_option('display.max_rows', 1000)

In [72]:
#filter out brands that are private label and no label that should not be our target customers
customer=customer[customer['brand_desc']!='PRIVATE LABEL']
customer=customer[customer['brand_desc']!='NO LABEL']

In [73]:
#if the customer has bought this product then we assign 1 to it.
customer['rating']=1

In [74]:
#only select the promoted products
customer=customer[customer['tran_prod_discount_amt']!=0]

In [75]:
customer

Unnamed: 0    prod_id   cust_id       tran_id     tran_dt  store_id  \
0                 1  145519008    799924  2.017111e+18  2017-11-12       349   
1                 2  145519008   1889991  2.017111e+18  2017-11-07       554   
2                 3  145519008   1889991  2.017111e+18  2017-11-13       554   
3                 4  145519008   2109544  2.017112e+18  2017-11-25       174   
7                 8  145519008   8639635  2.017103e+18  2017-10-28       313   
8                 9  145519008   8639635  2.017111e+18  2017-11-11       313   
10               11  145519008  11789884  2.017111e+18  2017-11-12       343   
12               13  145519008  16829885  2.017111e+18  2017-11-12       339   
14               15  145519008  18539540  2.017103e+18  2017-10-29       631   
17               18  145519008  18539540  2.017120e+18  2017-12-05       266   
18               19  145519008  18539540  2.017123e+18  2017-12-28       266   
19               20  145519008  18909750  2.017102e+18  2017-10-24       687   
20               21  145519008  18909750  2.017111e+18  2017-11-11       687   
21               22  145519008  18909750  2.017112e+18  2017-11-24       349   
22               23  145519008  21159716  2.017103e+18  2017-10-25       638   
23               24  145519008  21579922  2.017122e+18  2017-12-23       993   
24               25  145519008  24179544  2.017120e+18  2017-12-05       179   
26               27  145519008  26769899  2.017111e+18  2017-11-13       664   
27               28  145519008  27999642  2.017103e+18  2017-10-29       554   
29               30  145519008  31879773  2.017111e+18  2017-11-09       625   
30               31  145519008  37359574  2.017103e+18  2017-10-28       608   
31               32  145519008  37449943  2.017103e+18  2017-10-27       316   
33               34  145519008  38479729  2.017103e+18  2017-10-30       307   
37               38  145519008  41459822  2.017103e+18  2017-10-27       398   
40               41  145519008  41709665  2.017112e+18  2017-11-24       596   
44               45  145519008  47779590  2.017122e+18  2017-12-20       606   
48               49  145519008  51079908  2.017112e+18  2017-11-25       344   
49               50  145519008  52039852  2.017121e+18  2017-12-06       274   
55               56  145519008  56969964  2.017113e+18  2017-11-26       234   
57               58  145519008  59719949  2.017103e+18  2017-10-29       316   
58               59  145519008  59719949  2.017112e+18  2017-11-25       316   
59               60  145519008  61279763  2.017112e+18  2017-11-23       257   
60               61  145519008  62949989  2.017111e+18  2017-11-10       480   
61               62  145519008  63039914  2.017103e+18  2017-10-27       346   
63               64  145519008  64599801  2.017103e+18  2017-10-30       310   
64               65  145519008  64599801  2.017112e+18  2017-11-21       568   
65               66  145519008  66789769  2.017103e+18  2017-10-27       477   
66               67  145519008  66789769  2.017122e+18  2017-12-21       477   
74               75  145519008  74049890  2.017102e+18  2017-10-24       334   
78               79  145519008  78669634  2.017111e+18  2017-11-09       327   
81               82  145519008  79309672  2.017113e+18  2017-11-26       248   
82               83  145519008  79309672  2.017120e+18  2017-12-02       248   
85               86  145519008  81519841  2.017112e+18  2017-11-24       347   
86               87  145519008  81879929  2.017112e+18  2017-11-24       584   
87               88  145519008  82639994  2.017112e+18  2017-11-21       307   
88               89  145519008  82639994  2.017122e+18  2017-12-22       307   
91               92  145519008  84299911  2.017111e+18  2017-11-09       590   
92               93  145519008  85149539  2.017122e+18  2017-12-23       695   
93               94  145519008  87629985  2.017111e+18  2017-11-11       565   
94       

In [76]:
#prepare the original table into a table that used to calculate similarity score between two customers' purchase baskets
m=pd.pivot_table(customer,index ='cust_id', columns ='prod_id', values = 'rating').fillna(0)

In [77]:
m

prod_id   145519008  145519009  145519010  145519011  145519012  148066012  \
cust_id                                                                      
29568           0.0        0.0        0.0        0.0        0.0        0.0   
29909           0.0        0.0        0.0        0.0        0.0        0.0   
39856           0.0        0.0        0.0        0.0        0.0        0.0   
289996          0.0        0.0        0.0        0.0        0.0        0.0   
329968          0.0        0.0        1.0        0.0        0.0        0.0   
339627          0.0        0.0        0.0        0.0        0.0        0.0   
550000          0.0        0.0        0.0        1.0        1.0        0.0   
559804          0.0        0.0        0.0        0.0        0.0        0.0   
709543          0.0        0.0        0.0        0.0        0.0        0.0   
749639          0.0        0.0        0.0        0.0        0.0        0.0   
769883          0.0        0.0        0.0        0.0        0.0        0.0   
799924          1.0        0.0        0.0        0.0        1.0        0.0   
989587          0.0        0.0        0.0        0.0        0.0        0.0   
1139738         0.0        0.0        1.0        0.0        0.0        0.0   
1179795         0.0        0.0        0.0        0.0        0.0        1.0   
1459955         0.0        0.0        0.0        0.0        1.0        1.0   
1539803         0.0        0.0        0.0        0.0        0.0        0.0   
1589813         0.0        0.0        0.0        0.0        0.0        0.0   
1889991         1.0        1.0        1.0        0.0        0.0        0.0   
1979644         0.0        0.0        0.0        0.0        0.0        0.0   
2009974         0.0        0.0        0.0        0.0        0.0        0.0   
2029760         0.0        1.0        0.0        0.0        0.0        0.0   
2039621         0.0        0.0        0.0        0.0        0.0        0.0   
2089806         0.0        0.0        0.0        0.0        0.0        0.0   
2109544         1.0        0.0        1.0        1.0        0.0        0.0   
2169803         0.0        0.0        0.0        0.0        1.0        0.0   
2269534         0.0        0.0        0.0        0.0        0.0        1.0   
2569933         0.0        0.0        0.0        0.0        0.0        0.0   
2589576         0.0        0.0        0.0        0.0        0.0        0.0   
2629968         0.0        0.0        0.0        0.0        0.0        0.0   
2679893         0.0        0.0        0.0        0.0        0.0        0.0   
2719577         0.0        0.0        0.0        0.0        0.0        0.0   
2909908         0.0        0.0        0.0        0.0        0.0        0.0   
3029520         0.0        0.0        0.0        0.0        0.0        0.0   
3189829         0.0        0.0        0.0        0.0        0.0        0.0   
3239931         0.0        0.0        0.0        0.0        0.0        0.0   
3269902         0.0        0.0        0.0        0.0        0.0        0.0   
3409832         0.0        0.0        0.0        0.0        0.0        0.0   
3489829         0.0        0.0        0.0        0.0        0.0        0.0   
3509800         0.0        0.0        0.0        0.0        0.0        0.0   
3689815         0.0        0.0        0.0        0.0        0.0        0.0   
3689897         0.0        0.0        0.0        0.0        0.0        0.0   
3759797         0.0        0.0        0.0        0.0        0.0        0.0   
3779918         0.0        0.0        0.0        0.0        0.0        0.0   
3979821         0.0        0.0        0.0        0.0        0.0        0.0   
4139823         0.0        0.0        0.0        0.0        0.0        0.0   
4139886         0.0        0.0        0.0        0.0        0.0        0.0   
4149898         0.0        0.0        0.0        0.0        0.0        0.0   
4219822         0.0        0.0        0.0        0.0        0.0        0.0   
4459951         0.0   

In [80]:
#calculate the similarity score
cosine_sim = pd.DataFrame(1-pairwise_distances(m, metric="cosine"))

In [45]:
cosine_sim

0         1         2         3         4         5         6     \
0     1.000000  0.145913  0.160532  0.136753  0.112693  0.154232  0.182402   
1     0.145913  1.000000  0.168587  0.135266  0.185779  0.171765  0.167499   
2     0.160532  0.168587  1.000000  0.085088  0.157458  0.150848  0.208132   
3     0.136753  0.135266  0.085088  1.000000  0.117892  0.134240  0.113980   
4     0.112693  0.185779  0.157458  0.117892  1.000000  0.130478  0.169963   
5     0.154232  0.171765  0.150848  0.134240  0.130478  1.000000  0.176295   
6     0.182402  0.167499  0.208132  0.113980  0.169963  0.176295  1.000000   
7     0.160581  0.155666  0.185535  0.115783  0.145390  0.114414  0.141194   
8     0.227255  0.176300  0.182110  0.134252  0.184386  0.141316  0.197369   
9     0.115634  0.158150  0.125663  0.137635  0.146500  0.134529  0.118305   
10    0.148856  0.155113  0.155989  0.127346  0.127755  0.133215  0.141791   
11    0.221028  0.150011  0.199111  0.120723  0.111250  0.131175  0.166215   
12    0.165314  0.159597  0.169838  0.182298  0.164532  0.184059  0.182169   
13    0.117656  0.181030  0.136504  0.189900  0.148376  0.076150  0.132086   
14    0.122418  0.171414  0.137786  0.091068  0.175107  0.147899  0.164115   
15    0.140847  0.158234  0.143496  0.129662  0.211541  0.099262  0.137889   
16    0.125743  0.177678  0.174122  0.103731  0.188306  0.135639  0.175385   
17    0.108983  0.177951  0.141396  0.135509  0.160343  0.112858  0.128527   
18    0.091478  0.111902  0.091694  0.155780  0.131664  0.076883  0.106080   
19    0.169114  0.135569  0.161581  0.134872  0.170145  0.144223  0.184778   
20    0.174765  0.160059  0.160247  0.117009  0.112493  0.145161  0.138726   
21    0.107266  0.102884  0.137953  0.063656  0.188305  0.076578  0.134686   
22    0.148185  0.175386  0.167231  0.131648  0.182383  0.096401  0.146581   
23    0.113373  0.104426  0.152750  0.113858  0.190632  0.104359  0.159417   
24    0.130667  0.130842  0.133125  0.131227  0.188243  0.144710  0.179784   
25    0.183629  0.164745  0.247407  0.079035  0.186086  0.162993  0.203472   
26    0.152178  0.170592  0.227245  0.114622  0.163724  0.174661  0.159452   
27    0.165591  0.163238  0.152492  0.176379  0.166111  0.169747  0.129054   
28    0.099382  0.170597  0.119022  0.133077  0.156663  0.108634  0.108189   
29    0.153398  0.131659  0.206677  0.102703  0.100755  0.145615  0.139160   
30    0.160009  0.192513  0.220626  0.126864  0.195148  0.147530  0.180492   
31    0.166456  0.201639  0.155050  0.118875  0.171431  0.165352  0.200837   
32    0.133523  0.182616  0.155468  0.188726  0.185535  0.077670  0.188424   
33    0.159787  0.191220  0.223258  0.120354  0.191011  0.160872  0.207166   
34    0.141697  0.157561  0.179058  0.113006  0.183949  0.151052  0.150852   
35    0.120230  0.126037  0.111454  0.120745  0.183695  0.083801  0.145358   
36    0.110264  0.111488  0.127102  0.094125  0.139922  0.099911  0.120785   
37    0.182617  0.173405  0.183713  0.110039  0.181359  0.172090  0.219177   
38    0.194345  0.197387  0.231749  0.141336  0.166385  0.194316  0.210656   
39    0.161814  0.181621  0.155137  0.165965  0.201349  0.120625  0.196768   
40    0.189357  0.196757  0.234509  0.121016  0.174756  0.207974  0.193488   
41    0.171465  0.170592  0.212781  0.104226  0.209121  0.168996  0.184818   
42    0.142918  0.198956  0.193448  0.149510  0.183988  0.122305  0.181514   
43    0.158978  0.124800  0.148746  0.119744  0.175425  0.137192  0.156842   
44    0.120818  0.174959  0.160120  0.124904  0.203896  0.111621  0.159086   
45    0.131915  0.172102  0.151614  0.141027  0.159649  0.097680  0.162135   
46    0.174239  0.189404  0.222426  0.168622  0.202753  0.156924  0.202182   
47    0.132546  0.198798  0.151153  0.168349  0.184974  0.146006  0.170816   
48    0.167387  0.158208  0.175408  0.121876  0.203175  0.116282  0.163430   
49    0.156875  0.113171  0.122240  0.117150  0.164227  0.106913  0.137935   
50    0.170318  0.187183  0.2352

In [81]:
#label the dataframe with customer name correctly
cosine_sim.columns=m.index
cosine_sim.index=m.index

In [82]:
#replace the diagonal with 0 to avoid them being counted in the threshold list cuz they always equal 1
cosine_sim=cosine_sim.mask(cosine_sim == 1, 0)

In [48]:
cosine_sim

cust_id   29568     29909     39856     109693    289996    299749    \
cust_id                                                                
29568     0.000000  0.145913  0.160532  0.136753  0.112693  0.154232   
29909     0.145913  0.000000  0.168587  0.135266  0.185779  0.171765   
39856     0.160532  0.168587  0.000000  0.085088  0.157458  0.150848   
109693    0.136753  0.135266  0.085088  0.000000  0.117892  0.134240   
289996    0.112693  0.185779  0.157458  0.117892  0.000000  0.130478   
299749    0.154232  0.171765  0.150848  0.134240  0.130478  0.000000   
329968    0.182402  0.167499  0.208132  0.113980  0.169963  0.176295   
339627    0.160581  0.155666  0.185535  0.115783  0.145390  0.114414   
550000    0.227255  0.176300  0.182110  0.134252  0.184386  0.141316   
559804    0.115634  0.158150  0.125663  0.137635  0.146500  0.134529   
609881    0.148856  0.155113  0.155989  0.127346  0.127755  0.133215   
709543    0.221028  0.150011  0.199111  0.120723  0.111250  0.131175   
749556    0.165314  0.159597  0.169838  0.182298  0.164532  0.184059   
749639    0.117656  0.181030  0.136504  0.189900  0.148376  0.076150   
769883    0.122418  0.171414  0.137786  0.091068  0.175107  0.147899   
799924    0.140847  0.158234  0.143496  0.129662  0.211541  0.099262   
869947    0.125743  0.177678  0.174122  0.103731  0.188306  0.135639   
989587    0.108983  0.177951  0.141396  0.135509  0.160343  0.112858   
1049570   0.091478  0.111902  0.091694  0.155780  0.131664  0.076883   
1139738   0.169114  0.135569  0.161581  0.134872  0.170145  0.144223   
1179795   0.174765  0.160059  0.160247  0.117009  0.112493  0.145161   
1279966   0.107266  0.102884  0.137953  0.063656  0.188305  0.076578   
1329967   0.148185  0.175386  0.167231  0.131648  0.182383  0.096401   
1369576   0.113373  0.104426  0.152750  0.113858  0.190632  0.104359   
1459955   0.130667  0.130842  0.133125  0.131227  0.188243  0.144710   
1539803   0.183629  0.164745  0.247407  0.079035  0.186086  0.162993   
1589813   0.152178  0.170592  0.227245  0.114622  0.163724  0.174661   
1659549   0.165591  0.163238  0.152492  0.176379  0.166111  0.169747   
1849794   0.099382  0.170597  0.119022  0.133077  0.156663  0.108634   
1889991   0.153398  0.131659  0.206677  0.102703  0.100755  0.145615   
1979644   0.160009  0.192513  0.220626  0.126864  0.195148  0.147530   
1999671   0.166456  0.201639  0.155050  0.118875  0.171431  0.165352   
2009974   0.133523  0.182616  0.155468  0.188726  0.185535  0.077670   
2029760   0.159787  0.191220  0.223258  0.120354  0.191011  0.160872   
2039621   0.141697  0.157561  0.179058  0.113006  0.183949  0.151052   
2049977   0.120230  0.126037  0.111454  0.120745  0.183695  0.083801   
2089806   0.110264  0.111488  0.127102  0.094125  0.139922  0.099911   
2109544   0.182617  0.173405  0.183713  0.110039  0.181359  0.172090   
2169803   0.194345  0.197387  0.231749  0.141336  0.166385  0.194316   
2209804   0.161814  0.181621  0.155137  0.165965  0.201349  0.120625   
2269534   0.189357  0.196757  0.234509  0.121016  0.174756  0.207974   
2389981   0.171465  0.170592  0.212781  0.104226  0.209121  0.168996   
2469932   0.142918  0.198956  0.193448  0.149510  0.183988  0.122305   
2499933   0.158978  0.124800  0.148746  0.119744  0.175425  0.137192   
2569933   0.120818  0.174959  0.160120  0.124904  0.203896  0.111621   
2589576   0.131915  0.172102  0.151614  0.141027  0.159649  0.097680   
2629968   0.174239  0.189404  0.222426  0.168622  0.202753  0.156924   
2679893   0.132546  0.198798  0.151153  0.168349  0.184974  0.146006   
2719577   0.167387  0.158208  0.175408  0.121876  0.203175  0.116282   
2809801   0.156875  0.113171  0.122240  0.117150  0.164227  0.106913   
2899928   0.170318  0.187183  0.235267  0.120510  0.200752  0.182386   
2909908   0.117158  0.165708  0.149461  0.158585  0.174245  0.104620   
2969695   0.046364  0.093175  0.076348  0.126383  0.073086  0.096025   
3029520   0.216072  0.158312  0.254728  

In [49]:
#we can set a specific similarity threshold value but we didn't use this method
#get the list of customers that are above a certain similarity threshold
def threshold_list(score):
    threshold=pd.DataFrame(cosine_sim>score)
    s=set()
    stack=threshold.stack()
    ii = stack[stack == True].index.tolist()
    for i in range(len(ii)):
        s.add(ii[i][0])
        s.add(ii[i][1])
    cust_l=list(s)
    return cust_l

In [50]:
#we can set a specific similarity threshold value but we didn't use this method
#get the product bought by all the customers in the our threshold list
def get_product(cust_l):
    pro_s=set()
    for n in range(len(cust_l)):
        #one customer
        c_sub=customer[customer['cust_id']==cust_l[n]]
        #this customer's produts
        prod_l=list(c_sub['prod_id'])
        for i in range(len(prod_l)):
            pro_s.add(prod_l[i])
    return pro_s

In [16]:
#this is the method we use instead of setting a specific similarity threshold value
#select the top number of customer neighbors that are most similar with each customer
def get_top(top):
    top_l=list()
    for n in range(len(cosine_sim)):
        top_l.append(cosine_sim.nlargest(top,cosine_sim.index[n]).index.tolist())
    return top_l

In [87]:
#select 20 top most similar customers to narrow down the product pool used for recommender system
top_d=pd.DataFrame(get_top(20))

In [88]:
#assign the customer label to the previous table and check the outcome
top_d.index=cosine_sim.index
top_d

0         1         2         3         4         5   \
cust_id                                                                
29568     24719817  40549840  93789936    550000  75719956  64609833   
29909     39679904  23319645  65039971  52039852  99939955  36139969   
39856     96479520  33419626  16979906  65039971  75719956  66789769   
289996    76099948  58919615   3759797  16909799  99599996  65039971   
329968    65039971   9939955  63139548  74699977   9879865  73649581   
339627    27999642  73939814  54489828  37889608  61919896  36599872   
550000     2109544  46539873  13669829  64609833  16979906  23319645   
559804    87959993  73939814  88959959  41919552  36349611  62139531   
709543    40549840  24719817  79869845  73049516  96479520  70589922   
749639    65289953  85019945  41459822   2009974  42409790  77839901   
769883    70309838  10669538  99699822   3689897  60619555  33989662   
799924    71809833  83869839  20219866  72029993  99119952  46539981   
989587    99959807  86189590  42409790  66139812  83089666  53769798   
1139738   56969964  49709559  61719826  27899942  72369948  87279899   
1179795    2169803  70589922  55289819  96679586  90229683  95959691   
1459955   84659856  10669538  46539981  14509826  83149812  66019821   
1539803    3689897  60619555  25619583  56669670  38339836  48549830   
1589813   66789769   1539803  23319645   3689897  60619555  13669829   
1889991   93789936  73649581  24719817   2629968  85259620   2109544   
1979644   47389671  40549840  96779944   3689897  31069959  48419623   
2009974   48829987  59329765  61389597  81239800  27899942  44829828   
2029760   88589894  38339836  73939814  51939992  40549840   8489894   
2039621   65039971  68509954  87959993  45809866  23319833  86219926   
2089806   49709559  45539850  82499585  24319826  72369948  29649742   
2109544   76579825  47389671  59719949  11879968  66789769  56969964   
2169803   66789769  36779796  73649581  62139531  88589894  27999642   
2269534   73649581  66789769  27999642  26159683  38339836  54339975   
2569933   22009953  45289949  83869839  44829828  67379981  45229831   
2589576   65489581  58199923  88959959  73649581  83869839  53679928   
2629968   88959959  29519813  72759832  53679928  12949792  16269610   
2679893   10669538   3689897  84089627  71809833  79809829   3189829   
2719577   72369948  76099948  47519827  56209977  39139826  67379981   
2909908   27899942  67459546  83869839  82309911  49709559  82499585   
3029520   27999642  75719956  62139531  64019655  73649581  11879968   
3189829   76099948  72369948  30869590  71809833  49929918  63139548   
3239931   24719817  16979906   9879865     39856  66789769  59649884   
3269902   14259755  72609891  51939992   3689897  96229536  52039852   
3409832    3689897  45769973  76099948  49929918  45559604  38369823   
3489829   41459822  19199994  98729746  45229831  19349984    289996   
3509800   53849651  71809833  72029993  59329765  27899942  54279893   
3689815   77839901  61919896  35019716  40549840  27039629  25899797   
3689897   60619555  45769973  52039852   1539803  24719817   8489894   
3759797   45769973  70089938  32929755  58919615  82309982  63139548   
3779918   94499650  54099615   5039894  99119952  84089627  74699977   
3979821   73649581  15739825  99599996  72759832  87739997  82799808   
4139823   14259755  25619583  35119545  89869626  26769833  96779824   
4139886   72369948  21079546  30919566  65039971  93349625  63139548   
4149898   57949815  54489828  63039914  85019945  31429680  41459822   
4219822   60769795  76079817  14649887  96229536  48819714  38209579   
4459951   30699587  45959960  39139826  23319645  83869839  30349561   
4579768   65039971   1139738  47729807  21079546  61719826  29649742   
4729534   55289819  39729982  83869839  74699977     39856  24719817   
4759939   42409790  99119952  87629985  30919566  45959960  15739825   
4899809   82309911  47739935  88959959  72369948  744296

In [85]:
#label the customer table correctly with customer id
m['cust_id']=m.index

In [89]:
top_d.shape

(963, 20)

In [20]:
#Need a function that can take a customer ID as input and return a list of all the items they have purcahsed.
#Name: get_items Input: Customer ID(int) Output: List of items bought(List)
def get_items(customer_id):
    temp=m.loc[m["cust_id"]==customer_id]
    bought=list()
    for i,product in zip(range(len(temp.columns)),temp.columns):
        if(temp.iloc[0,i]==1):
           bought.append(product)
    return bought

In [21]:
#Make a dictionary of all the customers and their items bought
#name: get_scoreframe input: list of customer ids output: dict with key=customer id and value= list of products bought
def get_scoreframe(custs):
    mega=list()
    for customer in custs:
        mega=get_items(customer)+mega
    unique=set(mega)
    score=dict()
    for product in unique:
        score[product]=mega.count(product)
    scoreframe=pd.DataFrame.from_dict(score,orient="index")
    scoreframe['product']=scoreframe.index
    scoreframe.columns=['score','product']
    #calculate the probability
    scoreframe["score"]=scoreframe["score"]/len(custs)
    scoreframe['product']=pd.to_numeric(scoreframe['product'])    
    return scoreframe

In [94]:
#only select the relevant columns
increments=increments.loc[:,['prod_id','incremental']]

In [108]:
increments.sort_values(by='incremental')

prod_id  incremental
5148   999263658  -332.814926
5566   999273893  -237.182764
6513   999327531  -233.970219
6510   999327519  -180.671614
9722   999933661  -176.110000
4237   999240691  -171.968174
4065   999237328  -171.004114
7598   999403057  -162.940903
7207   999367749  -161.545459
3033   999196559  -149.809350
2232   999181113  -145.459484
6300   999306221  -139.166717
2637   999186926  -138.867637
6348   999308439  -129.470581
2665   999187504  -124.172780
1015   999162773  -119.095000
7385   999382485  -117.554625
7001   999355572  -113.005299
1515   999172001  -110.952489
7698   999422504  -108.864162
2017   999179112  -106.435000
2471   999184925  -105.550000
3117   999198658  -105.542802
5543   999273561  -104.065042
7556   999397940  -102.600770
3823   999233710  -101.470914
827    999159473  -100.170696
1919   999177966  -100.065000
5984   999297177   -99.707623
7924   999446742   -99.411142
331    999145784   -96.546014
3579   999229339   -96.480000
2895   999193957   -96.016000
4940   999257199   -93.983686
9787   999940407   -93.523042
8444   999525084   -92.910000
3362   999225211   -92.694721
6629   999332427   -92.368188
2821   999192416   -90.990000
9723   999933677   -88.898000
5678   999276595   -88.837364
3871   999233972   -88.370464
5774   999279415   -88.175159
3690   999231592   -87.385719
429    999151083   -86.701807
2283   999181500   -86.686262
2015   999179095   -86.293150
7198   999367535   -85.241312
4429   999245731   -84.908687
5550   999273572   -83.991831
2303   999181624   -83.619605
2449   999184766   -83.275238
2868   999193271   -82.643789
8440   999524183   -82.545801
6359   999308671   -82.489916
7417   999385161   -81.463291
10255  999988807   -81.417582
1325   999168441   -81.290000
3046   999196700   -80.905089
7636   999409919   -79.677676
4464   999246459   -79.618601
3140   999221668   -79.187799
7958   999451308   -77.973140
4715   999251394   -77.869966
4024   999236444   -77.242457
5047   999260428   -76.910000
770    999157927   -76.705374
10112  999969113   -76.654394
3321   999224762   -76.596417
5546   999273565   -76.366024
2966   999195977   -76.318294
3628   999230458   -76.217506
3906   999234259   -75.368039
8443   999524593   -75.165532
6715   999335874   -75.041378
1735   999175916   -73.688538
2660   999187323   -73.500000
995    999161979   -73.410415
1517   999172061   -73.178577
1136   999164337   -72.965237
8193   999485263   -72.615806
4330   999243576   -72.444667
4350   999243979   -72.389389
4570   999248329   -71.005960
3061   999197240   -70.920037
6403   999311184   -69.745044
7840   999439965   -69.562076
9472   999749587   -69.349207
3847   999233793   -68.602378
7548   999396299   -68.430322
5200   999264889   -68.421764
3915   999234312   -68.414710
1804   999176912   -68.100108
629    999156111   -67.554496
1077   999163815   -67.451118
3570   999229032   -67.196121
9668   999899623   -66.623883
8621   999557246   -66.565556
8049   999465471   -66.148740
5020   999259852   -65.927952
2255   999181222   -65.862853
8732   999590589   -65.815447
7066   999359083   -65.643901
5689   999276946   -65.245000
4021   999236128   -64.862341
693    999156752   -64.185563
1979   999178762   -63.720615
7386   999382622   -62.862584
7063   999358887   -62.821000
8037   999461159   -62.677928
2942   999195411   -62.356154
2014   999179092   -62.342000
4342   999243906   -62.323829
5360   999268768   -62.000769
881    999160025   -61.843272
1909   999177930   -61.671371
3374   999225371   -61.630704
6586   999330476   -61.584810
9901   999948167   -61.200209
10132  999971786   -60.959424
7451   999388473   -60.540179
5817   999286329   -60.498039
1921   999177968   -60.358314
5298   999267129   -60.354307
8715   999586494   -60.074174
8662   999571193   -60.025257
231    328781011   -60.016710
4422   999245599   -59.361220
7959   999451355   -58.897045
5303   999267179   -58.776745
8848   999622566   -58.763867
763    999157518   -57.885722
3      145519011   

In [90]:
#Make a function to return the top n recommneded products for each customer name: get_recommended_products 
#input: customer's scoreframe output: list of n products
def get_recommended_products(customer_frame):
    big_score=customer_frame.merge(increments,left_on='product',right_on='prod_id')
    big_score['ExpectedValue']=big_score['score']*big_score['incremental']
    #select the top 5 products
    return big_score.sort_values('ExpectedValue',ascending=False).loc[:,['product','ExpectedValue']].iloc[0:5,:]

In [105]:
#get the columns of expected value, cust_id and prod_id  
ExpectedValueFrame=pd.DataFrame()
for i in range(963):
    #get the customer's neighbors
    neighbors=top_d.iloc[i,:].tolist()
    #get the customer
    customer=top_d.index[i]
    #get the output of this customer
    output=pd.DataFrame(get_recommended_products(get_scoreframe(neighbors)))
    output['customer']=customer
    #append the output of this customer to a dataframe to have a complete list of customers
    ExpectedValueFrame=ExpectedValueFrame.append(output)


In [106]:
ExpectedValueFrame.head(10)

product  ExpectedValue  customer
1848  999168161      47.078725     29568
1849  999168163      41.273518     29568
1847  999168160      39.789200     29568
1717  999470815      37.963826     29568
1851  999168162      27.183463     29568
1748  999749460      14.527798     29568
933   999885829      14.146354     29568
1873  999749843      13.270833     29568
2167  999439575      10.822842     29568
1845  999168159       9.535723     29568

In [103]:
cd C:\Users\Jacky Yang\Desktop\Marketing Analytics\Recommend System

C:\Users\Jacky Yang\Desktop\Marketing Analytics\Recommend System
